In [1]:
using Revise; using QEDbase; using QEDprocesses; using MetagraphOptimization; using BenchmarkTools

In [2]:
QEDParticleTypeIn = Union{Type{FermionStateful{Incoming}},Type{AntiFermionStateful{Incoming}},Type{PhotonStateful{Incoming}}};
QEDParticleTypeOut = Union{Type{FermionStateful{Outgoing}}, Type{AntiFermionStateful{Outgoing}},Type{PhotonStateful{Outgoing}}};

PhotonTypes = Type{PhotonStateful}
FermionTypes = Union{Type{FermionStateful{Incoming}},Type{AntiFermionStateful{Outgoing}}};
AntifermionTypes = Union{Type{FermionStateful{Outgoing}},Type{AntiFermionStateful{Incoming}}};


In [8]:
function gen_diagram_helper(photons::Int, fermionsIn::Int, fermionsOut::Int, antifermionsIn::Int, antifermionsOut::Int, trace::String = "", fermionsN::Int = 1, photonsN::Int = 1)
    subtrace = "ph"
    if (fermionsIn == 1)
        subtrace *= " + f(in)"
    end
    if (antifermionsIn == 1)
        subtrace *= " + af(in)"
    end
    if (fermionsOut == 1)
        subtrace *= " + f(out)"
    end
    if (antifermionsOut == 1)
        subtrace *= " + af(out)"
    end
    if photons == 1 && (fermionsIn + antifermionsOut == 1) && (antifermionsIn + fermionsOut == 1)
        println("Average over $fermionsN fermion perturbations and sum over $photonsN photon perturbations for diagrams of form: $(trace)$(subtrace)")
        return nothing
    end
    
    #println("trace: $trace  photons: $(photons)  fermions: $(fermionsIn) / $fermionsOut  antifermions: $antifermionsIn / $antifermionsOut")

    if (photons != 0)
        if (fermionsIn != 0)
            # photon + fermionin
            gen_diagram_helper(photons - 1, fermionsIn, fermionsOut, antifermionsIn, antifermionsOut, trace * "ph + f(in) = f(in) -- ", fermionsN * fermionsIn, photonsN * photons)
        end
        if (fermionsOut != 0)
            # photon + fermionout
            gen_diagram_helper(photons - 1, fermionsIn + 1, fermionsOut, antifermionsIn, antifermionsOut, trace * "ph + f(out) = f(out) -- ", fermionsN * fermionsOut, photonsN * photons)
        end

        if (antifermionsIn != 0)
            # photon + antifermionin
            gen_diagram_helper(photons - 1, fermionsIn, fermionsOut, antifermionsIn, antifermionsOut, trace * "ph + af(in) = af(in) -- ", fermionsN * antifermionsIn, photonsN * photons)
        end
        if (antifermionsOut != 0)
            # photon + antifermionOut
            gen_diagram_helper(photons - 1, fermionsIn, fermionsOut, antifermionsIn, antifermionsOut, trace * "ph + af(out) = af(out) -- ", fermionsN * antifermionsOut, photonsN * photons)
        end

        if fermionsIn + fermionsOut + antifermionsIn + antifermionsOut != 0
            return nothing
        end
    end

    if (fermionsIn != 0)
        if (fermionsOut != 0)
            # fermionIn + fermionOut
            gen_diagram_helper(photons + 1, fermionsIn - 1, fermionsOut - 1, antifermionsIn, antifermionsOut, trace * "f(in) + f(out) = ph -- ", fermionsN * fermionsIn * fermionsOut, photonsN)
            return nothing
        end
        if (antifermionsIn != 0)
            #fermionIn + antfermionIn
            gen_diagram_helper(photons + 1, fermionsIn - 1, fermionsOut, antifermionsIn - 1, antifermionsOut, trace * "f(in) + af(in) = ph -- ", fermionsN * fermionsIn * antifermionsIn, photonsN)
            return nothing
        end
        #fermionIn + antifermionOut is impossible
    end

    if (fermionsOut != 0)
        if (antifermionsOut != 0)
            #fermionOut + antifermionOut
            gen_diagram_helper(photons + 1, fermionsIn, fermionsOut - 1, antifermionsIn, antifermionsOut - 1, trace * "f(out) + af(out) = ph -- ", fermionsN * fermionsOut * antifermionsOut, photonsN)
            return nothing
        end
        #fermionOut + antifermionIn is impossible
    end

    if (antifermionsIn != 0)
        if (antifermionsOut != 0)
            #antifermionIn + antifermionOut
            gen_diagram_helper(photons + 1, fermionsIn, fermionsOut, antifermionsIn - 1, antifermionsOut - 1, trace * "af(in) + af(out) = ph -- ", fermionsN * antifermionsIn * antifermionsOut, photonsN)
            return nothing
        end
    end
end

gen_diagram_helper (generic function with 4 methods)

In [4]:
# Compton:
gen_diagram_helper(2, 1, 1, 0, 0)

Average over 1 fermion perturbations and sum over 2 photon perturbations for diagrams of form: ph + f(in) = f(in) -- ph + f(in) + f(out)


In [5]:
# Pair annihilation
gen_diagram_helper(2, 1, 0, 1, 0)

Average over 1 fermion perturbations and sum over 2 photon perturbations for diagrams of form: ph + f(in) = f(in) -- ph + f(in) + af(in)
Average over 1 fermion perturbations and sum over 2 photon perturbations for diagrams of form: ph + af(in) = af(in) -- ph + f(in) + af(in)


In [6]:
# Pair production
gen_diagram_helper(2, 0, 1, 0, 1)

Average over 1 fermion perturbations and sum over 2 photon perturbations for diagrams of form: ph + af(out) = af(out) -- ph + f(out) + af(out)


In [7]:
# Trident
gen_diagram_helper(1, 1, 2, 0, 1)

Average over 2 fermion perturbations and sum over 1 photon perturbations for diagrams of form: ph + f(in) = f(in) -- f(in) + f(out) = ph -- ph + f(out) + af(out)
Average over 2 fermion perturbations and sum over 1 photon perturbations for diagrams of form: ph + af(out) = af(out) -- f(in) + f(out) = ph -- ph + f(out) + af(out)
